***

# Imports

In [1]:
# Imports all of the libraries that will be utilized throughout this project
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import statsmodels.api as sm
from datetime import datetime, timedelta

from io import StringIO
import requests

from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler, OneHotEncoder, MinMaxScaler
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import Ridge, Lasso
from sklearn.decomposition import PCA
from sklearn.metrics import mean_absolute_percentage_error
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestRegressor


# Enables view of all columns when viewing Pandas DataFrames
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# Private API Key utilized in the paramater variables below to extract data
api_key = ''


# itables import below
# from itables import init_notebook_mode
# init_notebook_mode(all_interactive=True)
# from itables import show

In [2]:
# Retrieves main set of data
api_url = "https://feeds.datagolf.com/historical-raw-data/rounds"

df_list = []

for year in range (2017, 2025):
    params = {
        'tour': 'pga',
        'event_id': 'all',
        'year': year,
        'file_format': 'csv',
        'key': api_key
    }

    response = requests.get(api_url, params=params)

    if response.status_code == 200:
        # Use StringIO to convert the response content into a file-like object for read_csv
        data = StringIO(response.text)
        df = pd.read_csv(data)
        df_list.append(df)
        print(f"Data added for year: {year}")
    else:
        print("Failed to fetch data from the API. Status code:", response.status_code)

tn_df = pd.concat(df_list, ignore_index=True)

print("\nData Retrieved!")

Data added for year: 2017
Data added for year: 2018
Data added for year: 2019
Data added for year: 2020
Data added for year: 2021
Data added for year: 2022
Data added for year: 2023
Data added for year: 2024

Data Retrieved!


In [3]:
# Retrieves main set of data
api_url = "https://feeds.datagolf.com/historical-raw-data/rounds"

df_list = []

for year in range (2024, 2025):
    params = {
        'tour': 'pga',
        'event_id': 'all',
        'year': year,
        'file_format': 'csv',
        'key': api_key
    }

    response = requests.get(api_url, params=params)

    if response.status_code == 200:
        # Use StringIO to convert the response content into a file-like object for read_csv
        data = StringIO(response.text)
        df = pd.read_csv(data)
        df_list.append(df)
        print(f"Data added for year: {year}")
    else:
        print("Failed to fetch data from the API. Status code:", response.status_code)

tt_df = pd.concat(df_list, ignore_index=True)

print("\nData Retrieved!")

Data added for year: 2024

Data Retrieved!


In [4]:
tn_df['year'].value_counts()

year
2019    19049
2023    18717
2022    18486
2021    18236
2018    18168
2017    18161
2020    14652
2024     4938
Name: count, dtype: int64

In [5]:
tt_df['year'].value_counts()

year
2024    4938
Name: count, dtype: int64

In [6]:
api_url = "https://feeds.datagolf.com/get-player-list"

params = {
    'file_format': 'csv',
    'key': api_key
}

response = requests.get(api_url, params=params)

if response.status_code == 200:
    # Use StringIO to convert the response content into a file-like object for read_csv
    data = StringIO(response.text)
    player_df = pd.read_csv(data)
else:
    print("Failed to fetch data from the API. Status code:", response.status_code)

player_df.to_csv('rank_df.csv', index=False)

In [7]:
api_url = 'https://feeds.datagolf.com/field-updates'

params = {
    'tour': 'pga',
    'file_format': 'csv',
    'key': api_key
}

response = requests.get(api_url, params=params)

if response.status_code == 200:
    # Use StringIO to convert the response content into a file-like object for read_csv
    data = StringIO(response.text)
    field_df = pd.read_csv(data)
else:
    print("Failed to fetch data from the API. Status code:", response.status_code)

field_df.to_csv('rank_df.csv', index=False)


***

# EDA

In [37]:
train_df = tn_df.copy()
test_df = tt_df.copy()

## Train Data Preprocessing

In [38]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 130407 entries, 0 to 130406
Data columns (total 30 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   tour             130407 non-null  object 
 1   year             130407 non-null  int64  
 2   season           130407 non-null  int64  
 3   event_completed  130407 non-null  object 
 4   event_name       130407 non-null  object 
 5   event_id         130407 non-null  int64  
 6   player_name      130407 non-null  object 
 7   dg_id            130407 non-null  int64  
 8   fin_text         130407 non-null  object 
 9   round_num        130407 non-null  int64  
 10  course_name      130407 non-null  object 
 11  course_num       130407 non-null  int64  
 12  course_par       130407 non-null  int64  
 13  start_hole       130407 non-null  int64  
 14  teetime          130407 non-null  object 
 15  round_score      129947 non-null  float64
 16  sg_putt          103238 non-null  floa

In [39]:
# convert dates
train_df['event_completed'] = train_df['event_completed'].astype('datetime64[ns]')

In [40]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 130407 entries, 0 to 130406
Data columns (total 30 columns):
 #   Column           Non-Null Count   Dtype         
---  ------           --------------   -----         
 0   tour             130407 non-null  object        
 1   year             130407 non-null  int64         
 2   season           130407 non-null  int64         
 3   event_completed  130407 non-null  datetime64[ns]
 4   event_name       130407 non-null  object        
 5   event_id         130407 non-null  int64         
 6   player_name      130407 non-null  object        
 7   dg_id            130407 non-null  int64         
 8   fin_text         130407 non-null  object        
 9   round_num        130407 non-null  int64         
 10  course_name      130407 non-null  object        
 11  course_num       130407 non-null  int64         
 12  course_par       130407 non-null  int64         
 13  start_hole       130407 non-null  int64         
 14  teetime          130

In [41]:
# Remove nulls
train_df = train_df.dropna(axis=0)

In [42]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 98625 entries, 0 to 130406
Data columns (total 30 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             98625 non-null  object        
 1   year             98625 non-null  int64         
 2   season           98625 non-null  int64         
 3   event_completed  98625 non-null  datetime64[ns]
 4   event_name       98625 non-null  object        
 5   event_id         98625 non-null  int64         
 6   player_name      98625 non-null  object        
 7   dg_id            98625 non-null  int64         
 8   fin_text         98625 non-null  object        
 9   round_num        98625 non-null  int64         
 10  course_name      98625 non-null  object        
 11  course_num       98625 non-null  int64         
 12  course_par       98625 non-null  int64         
 13  start_hole       98625 non-null  int64         
 14  teetime          98625 non-null  object   

In [43]:
def round_date(train_df):
    if train_df['round_num'] == 1:
        return train_df['event_completed'] - pd.Timedelta(days=3)
    elif train_df['round_num'] == 2:
        return train_df['event_completed'] - pd.Timedelta(days=2)
    elif train_df['round_num'] == 3:
        return train_df['event_completed'] - pd.Timedelta(days=1)
    else:
        return train_df['event_completed']


train_df['round_completed'] = train_df.apply(round_date,axis=1)

In [44]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 98625 entries, 0 to 130406
Data columns (total 31 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             98625 non-null  object        
 1   year             98625 non-null  int64         
 2   season           98625 non-null  int64         
 3   event_completed  98625 non-null  datetime64[ns]
 4   event_name       98625 non-null  object        
 5   event_id         98625 non-null  int64         
 6   player_name      98625 non-null  object        
 7   dg_id            98625 non-null  int64         
 8   fin_text         98625 non-null  object        
 9   round_num        98625 non-null  int64         
 10  course_name      98625 non-null  object        
 11  course_num       98625 non-null  int64         
 12  course_par       98625 non-null  int64         
 13  start_hole       98625 non-null  int64         
 14  teetime          98625 non-null  object   

In [45]:
train_df.head()

tour  year  season event_completed                   event_name  event_id  \
0  pga  2017    2017      2017-01-08  SBS Tournament of Champions        16   
1  pga  2017    2017      2017-01-08  SBS Tournament of Champions        16   
2  pga  2017    2017      2017-01-08  SBS Tournament of Champions        16   
4  pga  2017    2017      2017-01-08  SBS Tournament of Champions        16   
5  pga  2017    2017      2017-01-08  SBS Tournament of Champions        16   

     player_name  dg_id fin_text  round_num                   course_name  \
0    Herman, Jim  12846      T12          1  Plantation Course at Kapalua   
1  Gomez, Fabian   8571       20          1  Plantation Course at Kapalua   
2  Knox, Russell  13831      T17          4  Plantation Course at Kapalua   
4  Knox, Russell  13831      T17          2  Plantation Course at Kapalua   
5  Knox, Russell  13831      T17          1  Plantation Course at Kapalua   

   course_num  course_par  start_hole  teetime  round_score  sg_putt  sg_arg  \
0         656          73           1  11:20am         67.0    1.248  -0.605   
1         656          73           1  11:30am         70.0    1.832   0.357   
2         656          73           1   9:35am         73.0    0.885   0.378   
4         656          73           1  11:10am         69.0    1.211   1.257   
5         656          73           1  12:30pm         71.0   -0.126  -0.373   

   sg_app  sg_ott  sg_t2g  sg_total  driving_dist  driving_acc    gir  \
0   2.353   0.347   2.095     3.344         292.8        0.867  0.889   
1  -1.338  -0.507  -1.489     0.344         281.6        0.733  0.722   
2  -1.844  -1.294  -2.760    -1.875         288.2        0.533  0.778   
4  -1.412   0.037  -0.118     1.094         282.6        0.933  0.667   
5   1.473  -1.629  -0.530    -0.656         280.7        0.733  0.833   

   scrambling  prox_rgh  prox_fw  great_shots  poor_shots round_completed  
0       0.667    27.051   21.601          3.0         2.0      2017-01-05  
1       0.625    70.450   40.227          4.0         1.0      2017-01-05  
2       0.500    28.339   33.636          1.0         6.0      2017-01-08  
4       1.000    26.804   39.292          2.0         4.0      2017-01-06  
5       1.000    23.548   31.604          3.0         3.0      2017-01-05

In [46]:
train_df['month'] = train_df['round_completed'].dt.month
train_df['day'] = train_df['round_completed'].dt.day

In [47]:
train_df.tail()

tour  year  season event_completed            event_name  event_id  \
130402  pga  2024    2024      2024-03-24  Valspar Championship       475   
130403  pga  2024    2024      2024-03-24  Valspar Championship       475   
130404  pga  2024    2024      2024-03-24  Valspar Championship       475   
130405  pga  2024    2024      2024-03-24  Valspar Championship       475   
130406  pga  2024    2024      2024-03-24  Valspar Championship       475   

             player_name  dg_id fin_text  round_num  \
130402  Tosti, Alejandro  17032      T75          4   
130403  Hoffman, Charley   5768      CUT          1   
130404  Hoffman, Charley   5768      CUT          2   
130405     Coody, Parker  27870      T67          4   
130406  Pendrith, Taylor  17780      CUT          2   

                                  course_name  course_num  course_par  \
130402  Innisbrook Resort (Copperhead Course)         665          71   
130403  Innisbrook Resort (Copperhead Course)         665          71   
130404  Innisbrook Resort (Copperhead Course)         665          71   
130405  Innisbrook Resort (Copperhead Course)         665          71   
130406  Innisbrook Resort (Copperhead Course)         665          71   

        start_hole teetime  round_score  sg_putt  sg_arg  sg_app  sg_ott  \
130402           1  8:07AM         77.0   -4.623   0.296  -0.968  -0.361   
130403          10  2:02PM         72.0   -1.867   0.610   1.317  -0.988   
130404           1  8:52AM         71.0   -1.663   0.543   1.001   0.983   
130405           1  8:16AM         72.0    0.073  -0.283  -0.552   0.106   
130406          10  7:51AM         72.0    1.527  -0.595  -1.355   0.287   

        sg_t2g  sg_total  driving_dist  driving_acc    gir  scrambling  \
130402  -1.032    -5.649         297.6        0.462  0.444       0.462   
130403   0.940    -0.928         285.0        0.231  0.500       0.727   
130404   2.527     0.864         284.4        0.615  0.667       0.857   
130405  -0.728    -0.649         277.9        0.462  0.444       0.667   
130406  -1.663    -0.136         300.6        0.462  0.556       0.636   

        prox_rgh  prox_fw  great_shots  poor_shots round_completed  month  day  
130402    57.422   32.144          3.0         7.0      2024-03-24      3   24  
130403    42.518   23.829          3.0         5.0      2024-03-21      3   21  
130404    60.479   34.941          4.0         5.0      2024-03-22      3   22  
130405    34.259   45.341          2.0         1.0      2024-03-24      3   24  
130406    54.621   32.916          5.0         5.0      2024-03-22      3   22

In [48]:
train_df['fin_num'] = train_df['fin_text'].str.extract('(\d+)')
train_df.loc[train_df['fin_num'].isna(), 'fin_num'] = '0'
train_df['fin_num'] = train_df['fin_num'].astype(int)
train_df = train_df.drop(['fin_text'], axis=1)

In [49]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 98625 entries, 0 to 130406
Data columns (total 33 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             98625 non-null  object        
 1   year             98625 non-null  int64         
 2   season           98625 non-null  int64         
 3   event_completed  98625 non-null  datetime64[ns]
 4   event_name       98625 non-null  object        
 5   event_id         98625 non-null  int64         
 6   player_name      98625 non-null  object        
 7   dg_id            98625 non-null  int64         
 8   round_num        98625 non-null  int64         
 9   course_name      98625 non-null  object        
 10  course_num       98625 non-null  int64         
 11  course_par       98625 non-null  int64         
 12  start_hole       98625 non-null  int64         
 13  teetime          98625 non-null  object        
 14  round_score      98625 non-null  float64  

In [50]:
#
train_df['teetime_cleaned'] = pd.to_datetime(train_df['teetime'], format='%I:%M%p').dt.time
train_df['teetime_numeric'] = train_df['teetime_cleaned'].apply(lambda x: x.hour + x.minute / 60)
train_df = train_df.drop(['teetime','teetime_cleaned'], axis=1)

In [51]:
train_df['ohe_win'] = np.where(train_df['fin_num'] == 1, 1, 0)
train_df['ohe_top_five'] = np.where(train_df['fin_num'] <= 5, 1, 0)
train_df['ohe_top_ten'] = np.where(train_df['fin_num'] <= 10, 1, 0)
train_df['ohe_top_twenty'] = np.where(train_df['fin_num'] <= 20, 1, 0)
train_df['ohe_make_cut'] = np.where(train_df['fin_num'] == 0, 1, 0)

In [52]:
train_df_sorted = train_df.sort_values(by=['year', 'dg_id','round_completed'], ascending=[True,True,True])

In [53]:
train_df_sorted['L20_moving_avg_sg_putt'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_sg_putt'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_sg_putt'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_sg_putt'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_sg_putt'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_sg_arg'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_sg_arg'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_sg_arg'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_sg_arg'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_sg_arg'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_sg_app'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_sg_app'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_sg_app'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_sg_app'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_sg_app'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_sg_ott'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_sg_ott'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_sg_ott'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_sg_ott'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_sg_ott'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_sg_t2g'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_sg_t2g'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_sg_t2g'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_sg_t2g'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_sg_t2g'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_sg_total'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_sg_total'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_sg_total'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_sg_total'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_sg_total'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_driving_dist'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_driving_dist'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_driving_dist'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_driving_dist'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_driving_dist'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_driving_acc'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_driving_acc'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_driving_acc'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_driving_acc'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_driving_acc'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_gir'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_gir'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_gir'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_gir'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_gir'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


train_df_sorted['L20_moving_avg_scrambling'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg_scrambling'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg_scrambling'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg_scrambling'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg_scrambling'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())

In [54]:
train_df_sorted['career_avg'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).mean())
train_df_sorted['L20_moving_avg'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
train_df_sorted['L16_moving_avg'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
train_df_sorted['L12_moving_avg'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
train_df_sorted['L8_moving_avg'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
train_df_sorted['L4_moving_avg'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())

train_df_sorted['career_min'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).min())
train_df_sorted['L20_moving_min'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).min())
train_df_sorted['L16_moving_min'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).min())
train_df_sorted['L12_moving_min'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).min())
train_df_sorted['L8_moving_min'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).min())
train_df_sorted['L4_moving_min'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).min())

train_df_sorted['career_max'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).max())
train_df_sorted['L20_moving_max'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).max())
train_df_sorted['L16_moving_max'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).max())
train_df_sorted['L12_moving_max'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).max())
train_df_sorted['L8_moving_max'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).max())
train_df_sorted['L4_moving_max'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).max())

In [55]:
# train_df_sorted['career_round_score_std_dev'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_round_score_std_dev'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_round_score_std_dev'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_round_score_std_dev'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_round_score_std_dev'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_round_score_std_dev'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_sg_putt_std_dev'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_sg_putt_std_dev'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16__sg_putt_std_dev'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_putt_std_dev'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_putt_std_dev'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_sg_putt_std_dev'] = train_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_sg_arg_std_dev'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_sg_arg_std_dev'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_sg_arg_std_dev'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_sg_arg_std_dev'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_sg_arg_std_dev'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_sg_arg_std_dev'] = train_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_sg_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_sg_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_sg_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_sg_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_sg_ott_std_dev'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_sg_ott_std_dev'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_sg_ott_std_dev'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_sg_ott_std_dev'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_sg_ott_std_dev'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_sg_ott_std_dev'] = train_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_sg_t2g_std_dev'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_sg_t2g_std_dev'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_sg_t2g_std_dev'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_sg_t2g_std_dev'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_sg_t2g_std_dev'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_sg_t2g_std_dev'] = train_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_sg_total_std_dev'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_sg_total_std_dev'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_sg_total_std_dev'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_sg_total_std_dev'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_total_std_dev'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_sg_total_std_dev'] = train_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_driving_dist_std_dev'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_driving_dist_std_dev'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_driving_dist_std_dev'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_driving_dist_std_dev'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_driving_dist_std_dev'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_driving_dist_std_dev'] = train_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_driving_acc_std_dev'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_driving_acc_std_dev'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_driving_acc_std_dev'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_driving_acc_std_dev'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_driving_acc_std_dev'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_driving_acc_std_dev'] = train_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_gir_std_dev'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_gir_std_dev'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_gir_std_dev'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_gir_std_dev'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_gir_std_dev'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_gir_std_dev'] = train_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# train_df_sorted['career_scrambling_std_dev'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.expanding(min_periods=1).std())
train_df_sorted['L20_scrambling_std_dev'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
train_df_sorted['L16_scrambling_std_dev'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
train_df_sorted['L12_scrambling_std_dev'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
train_df_sorted['L8_scrambling_std_dev'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
train_df_sorted['L4_scrambling_std_dev'] = train_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/1923709744.py:25: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_df_sorted['L12_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/1923709744.py:26: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_df_sorted['L8_sg_app_std_dev'] = train_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=8,

In [56]:
now = datetime.now()

# Calculate days since each round
train_df_sorted['Days_Since'] = (now - train_df_sorted['round_completed']).dt.days

train_df_sorted['Last_365_Days'] = np.where(train_df_sorted['Days_Since'] <= 365, 1, 0)
train_df_sorted['Last_180_Days'] = np.where(train_df_sorted['Days_Since'] <= 180, 1, 0)
train_df_sorted['Last_90_Days'] = np.where(train_df_sorted['Days_Since'] <= 90, 1, 0)
train_df_sorted['Last_60_Days'] = np.where(train_df_sorted['Days_Since'] <= 60, 1, 0)
train_df_sorted['Last_30_Days'] = np.where(train_df_sorted['Days_Since'] <= 30, 1, 0)
train_df_sorted['Last_10_Days'] = np.where(train_df_sorted['Days_Since'] <= 10, 1, 0)
train_df_sorted['Last_5_Days'] = np.where(train_df_sorted['Days_Since'] <= 5, 1, 0)

/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2619049705.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_df_sorted['Days_Since'] = (now - train_df_sorted['round_completed']).dt.days
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2619049705.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_df_sorted['Last_365_Days'] = np.where(train_df_sorted['Days_Since'] <= 365, 1, 0)
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2619049705.py:7: PerformanceWarning: DataF

In [57]:
# train_df_sorted['career_rounds_played'] = train_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).count())

In [58]:
train_df_sorted['lagged_year'] = train_df_sorted.groupby('dg_id')['year'].shift(1)
train_df_sorted['lagged_season'] = train_df_sorted.groupby('dg_id')['season'].shift(1)
train_df_sorted['lagged_event_id'] = train_df_sorted.groupby('dg_id')['event_id'].shift(1)
train_df_sorted['lagged_round_num'] = train_df_sorted.groupby('dg_id')['round_num'].shift(1)
train_df_sorted['lagged_course_num'] = train_df_sorted.groupby('dg_id')['course_num'].shift(1)
train_df_sorted['lagged_course_par'] = train_df_sorted.groupby('dg_id')['course_par'].shift(1)
train_df_sorted['lagged_start_hole'] = train_df_sorted.groupby('dg_id')['start_hole'].shift(1)
train_df_sorted['lagged_round_score'] = train_df_sorted.groupby('dg_id')['round_score'].shift(1)
train_df_sorted['lagged_sg_putt'] = train_df_sorted.groupby('dg_id')['sg_putt'].shift(1)
train_df_sorted['lagged_sg_arg'] = train_df_sorted.groupby('dg_id')['sg_arg'].shift(1)
train_df_sorted['lagged_sg_app'] = train_df_sorted.groupby('dg_id')['sg_app'].shift(1)
train_df_sorted['lagged_sg_ott'] = train_df_sorted.groupby('dg_id')['sg_ott'].shift(1)
train_df_sorted['lagged_sg_t2g'] = train_df_sorted.groupby('dg_id')['sg_t2g'].shift(1)
train_df_sorted['lagged_sg_total'] = train_df_sorted.groupby('dg_id')['sg_total'].shift(1)
train_df_sorted['lagged_driving_dist'] = train_df_sorted.groupby('dg_id')['driving_dist'].shift(1)
train_df_sorted['lagged_driving_acc'] = train_df_sorted.groupby('dg_id')['driving_acc'].shift(1)
train_df_sorted['lagged_gir'] = train_df_sorted.groupby('dg_id')['gir'].shift(1)
train_df_sorted['lagged_scrambling'] = train_df_sorted.groupby('dg_id')['scrambling'].shift(1)
train_df_sorted['lagged_prox_rgh'] = train_df_sorted.groupby('dg_id')['prox_rgh'].shift(1)
train_df_sorted['lagged_prox_fw'] = train_df_sorted.groupby('dg_id')['prox_fw'].shift(1)
train_df_sorted['lagged_great_shots'] = train_df_sorted.groupby('dg_id')['great_shots'].shift(1)
train_df_sorted['lagged_poor_shots'] = train_df_sorted.groupby('dg_id')['poor_shots'].shift(1)
train_df_sorted['lagged_month'] = train_df_sorted.groupby('dg_id')['month'].shift(1)
train_df_sorted['lagged_day'] = train_df_sorted.groupby('dg_id')['day'].shift(1)
train_df_sorted['lagged_fin_num'] = train_df_sorted.groupby('dg_id')['fin_num'].shift(1)
train_df_sorted['lagged_teetime_numeric'] = train_df_sorted.groupby('dg_id')['teetime_numeric'].shift(1)
train_df_sorted['lagged_ohe_win'] = train_df_sorted.groupby('dg_id')['ohe_win'].shift(1)
train_df_sorted['lagged_ohe_top_five'] = train_df_sorted.groupby('dg_id')['ohe_top_five'].shift(1)
train_df_sorted['lagged_ohe_top_ten'] = train_df_sorted.groupby('dg_id')['ohe_top_ten'].shift(1)
train_df_sorted['lagged_ohe_top_twenty'] = train_df_sorted.groupby('dg_id')['ohe_top_twenty'].shift(1)
train_df_sorted['lagged_ohe_make_cut'] = train_df_sorted.groupby('dg_id')['ohe_make_cut'].shift(1)

/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2889363970.py:1: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_df_sorted['lagged_year'] = train_df_sorted.groupby('dg_id')['year'].shift(1)
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2889363970.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  train_df_sorted['lagged_season'] = train_df_sorted.groupby('dg_id')['season'].shift(1)
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2889363970.py:3: PerformanceWarning: DataFr

In [59]:
train_df_sorted.info()

<class 'pandas.core.frame.DataFrame'>
Index: 98625 entries, 1092 to 128293
Columns: 200 entries, tour to lagged_ohe_make_cut
dtypes: datetime64[ns](2), float64(170), int32(2), int64(22), object(4)
memory usage: 150.5+ MB


In [60]:
train_df_sorted.isna().sum()

tour                              0
year                              0
season                            0
event_completed                   0
event_name                        0
event_id                          0
player_name                       0
dg_id                             0
round_num                         0
course_name                       0
course_num                        0
course_par                        0
start_hole                        0
round_score                       0
sg_putt                           0
sg_arg                            0
sg_app                            0
sg_ott                            0
sg_t2g                            0
sg_total                          0
driving_dist                      0
driving_acc                       0
gir                               0
scrambling                        0
prox_rgh                          0
prox_fw                           0
great_shots                       0
poor_shots                  

In [61]:
train_df_sorted = train_df_sorted.dropna(axis=0)

In [62]:
train_df_sorted.isna().sum()

tour                           0
year                           0
season                         0
event_completed                0
event_name                     0
event_id                       0
player_name                    0
dg_id                          0
round_num                      0
course_name                    0
course_num                     0
course_par                     0
start_hole                     0
round_score                    0
sg_putt                        0
sg_arg                         0
sg_app                         0
sg_ott                         0
sg_t2g                         0
sg_total                       0
driving_dist                   0
driving_acc                    0
gir                            0
scrambling                     0
prox_rgh                       0
prox_fw                        0
great_shots                    0
poor_shots                     0
round_completed                0
month                          0
day       

In [63]:
train_df_sorted.loc[train_df_sorted['player_name'] == 'Malnati, Peter',]

tour  year  season event_completed  \
353     pga  2017    2017      2017-01-15   
339     pga  2017    2017      2017-01-15   
346     pga  2017    2017      2017-01-15   
616     pga  2017    2017      2017-01-22   
615     pga  2017    2017      2017-01-22   
1396    pga  2017    2017      2017-01-29   
2320    pga  2017    2017      2017-02-12   
2933    pga  2017    2017      2017-02-19   
2932    pga  2017    2017      2017-02-19   
2931    pga  2017    2017      2017-02-19   
2930    pga  2017    2017      2017-02-19   
2986    pga  2017    2017      2017-02-26   
2985    pga  2017    2017      2017-02-26   
4054    pga  2017    2017      2017-03-12   
3805    pga  2017    2017      2017-03-12   
5090    pga  2017    2017      2017-04-02   
5091    pga  2017    2017      2017-04-02   
5785    pga  2017    2017      2017-04-16   
5786    pga  2017    2017      2017-04-16   
5787    pga  2017    2017      2017-04-16   
5788    pga  2017    2017      2017-04-16   
6046    pga  2017    2017      2017-04-23   
6047    pga  2017    2017      2017-04-23   
6740    pga  2017    2017      2017-05-07   
6728    pga  2017    2017      2017-05-07   
7088    pga  2017    2017      2017-05-14   
7089    pga  2017    2017      2017-05-14   
7445    pga  2017    2017      2017-05-21   
7444    pga  2017    2017      2017-05-21   
7443    pga  2017    2017      2017-05-21   
7442    pga  2017    2017      2017-05-21   
8992    pga  2017    2017      2017-06-11   
8993    pga  2017    2017      2017-06-11   
9920    pga  2017    2017      2017-06-25   
9921    pga  2017    2017      2017-06-25   
9922    pga  2017    2017      2017-06-25   
10202   pga  2017    2017      2017-07-02   
10203   pga  2017    2017      2017-07-02   
10204   pga  2017    2017      2017-07-02   
10817   pga  2017    2017      2017-07-09   
10820   pga  2017    2017      2017-07-09   
10841   pga  2017    2017      2017-07-09   
10840   pga  2017    2017      2017-07-09   
10915   pga  2017    2017      2017-07-16   
10897   pga  2017    2017      2017-07-16   
10916   pga  2017    2017      2017-07-16   
10917   pga  2017    2017      2017-07-16   
12162   pga  2017    2017      2017-07-23   
12161   pga  2017    2017      2017-07-23   
12133   pga  2017    2017      2017-07-23   
12158   pga  2017    2017      2017-07-23   
12553   pga  2017    2017      2017-07-30   
12552   pga  2017    2017      2017-07-30   
12551   pga  2017    2017      2017-07-30   
12550   pga  2017    2017      2017-07-30   
13421   pga  2017    2017      2017-08-20   
13420   pga  2017    2017      2017-08-20   
13419   pga  2017    2017      2017-08-20   
13418   pga  2017    2017      2017-08-20   
15046   pga  2017    2018      2017-10-08   
15047   pga  2017    2018      2017-10-08   
15048   pga  2017    2018      2017-10-08   
15049   pga  2017    2018      2017-10-08   
16461   pga  2017    2018      2017-10-29   
16433   pga  2017    2018      2017-10-29   
16458   pga  2017    2018      2017-10-29   
16432   pga  2017    2018      2017-10-29   
16923   pga  2017    2018      2017-11-05   
16924   pga  2017    2018      2017-11-05   
16925   pga  2017    2018      2017-11-05   
16926   pga  2017    2018      2017-11-05   
17833   pga  2017    2018      2017-11-19   
18303   pga  2018    2018      2018-01-14   
18298   pga  2018    2018      2018-01-14   
18910   pga  2018    2018      2018-01-21   
19546   pga  2018    2018      2018-01-28   
19769   pga  2018    2018      2018-02-04   
19760   pga  2018    2018      2018-02-04   
20201   pga  2018    2018      2018-02-11   
20203   pga  2018    2018      2018-02-11   
20695   pga  2018    2018      2018-02-18   
20694   pga  2018    2018      2018-02-18   
21195   pga  2018    2018      2018-02-25   
21194   pga  2018    2018      2018-02-25   
21193   pga  2018    2018      2018-02-25   
21192   pga  2018    2018      2018-02-25   
21935   pga  2018    2018      2018-03-11   
21950   pga  2018    2018      2018-03-11   
23

## Test Data Preprocessing

In [64]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4938 entries, 0 to 4937
Data columns (total 30 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   tour             4938 non-null   object 
 1   year             4938 non-null   int64  
 2   season           4938 non-null   int64  
 3   event_completed  4938 non-null   object 
 4   event_name       4938 non-null   object 
 5   event_id         4938 non-null   int64  
 6   player_name      4938 non-null   object 
 7   dg_id            4938 non-null   int64  
 8   fin_text         4938 non-null   object 
 9   round_num        4938 non-null   int64  
 10  course_name      4938 non-null   object 
 11  course_num       4938 non-null   int64  
 12  course_par       4938 non-null   int64  
 13  start_hole       4938 non-null   int64  
 14  teetime          4938 non-null   object 
 15  round_score      4938 non-null   int64  
 16  sg_putt          3932 non-null   float64
 17  sg_arg        

In [65]:
# convert dates
test_df['event_completed'] = test_df['event_completed'].astype('datetime64[ns]')

In [66]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4938 entries, 0 to 4937
Data columns (total 30 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             4938 non-null   object        
 1   year             4938 non-null   int64         
 2   season           4938 non-null   int64         
 3   event_completed  4938 non-null   datetime64[ns]
 4   event_name       4938 non-null   object        
 5   event_id         4938 non-null   int64         
 6   player_name      4938 non-null   object        
 7   dg_id            4938 non-null   int64         
 8   fin_text         4938 non-null   object        
 9   round_num        4938 non-null   int64         
 10  course_name      4938 non-null   object        
 11  course_num       4938 non-null   int64         
 12  course_par       4938 non-null   int64         
 13  start_hole       4938 non-null   int64         
 14  teetime          4938 non-null   object 

In [67]:
# Remove nulls
test_df = test_df.dropna(axis=0)

In [68]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3836 entries, 0 to 4937
Data columns (total 30 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             3836 non-null   object        
 1   year             3836 non-null   int64         
 2   season           3836 non-null   int64         
 3   event_completed  3836 non-null   datetime64[ns]
 4   event_name       3836 non-null   object        
 5   event_id         3836 non-null   int64         
 6   player_name      3836 non-null   object        
 7   dg_id            3836 non-null   int64         
 8   fin_text         3836 non-null   object        
 9   round_num        3836 non-null   int64         
 10  course_name      3836 non-null   object        
 11  course_num       3836 non-null   int64         
 12  course_par       3836 non-null   int64         
 13  start_hole       3836 non-null   int64         
 14  teetime          3836 non-null   object      

In [69]:
def round_date(test_df):
    if test_df['round_num'] == 1:
        return test_df['event_completed'] - pd.Timedelta(days=3)
    elif test_df['round_num'] == 2:
        return test_df['event_completed'] - pd.Timedelta(days=2)
    elif test_df['round_num'] == 3:
        return test_df['event_completed'] - pd.Timedelta(days=1)
    else:
        return test_df['event_completed']


test_df['round_completed'] = test_df.apply(round_date,axis=1)

In [70]:
test_df['month'] = test_df['round_completed'].dt.month
test_df['day'] = test_df['round_completed'].dt.day

In [71]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3836 entries, 0 to 4937
Data columns (total 33 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             3836 non-null   object        
 1   year             3836 non-null   int64         
 2   season           3836 non-null   int64         
 3   event_completed  3836 non-null   datetime64[ns]
 4   event_name       3836 non-null   object        
 5   event_id         3836 non-null   int64         
 6   player_name      3836 non-null   object        
 7   dg_id            3836 non-null   int64         
 8   fin_text         3836 non-null   object        
 9   round_num        3836 non-null   int64         
 10  course_name      3836 non-null   object        
 11  course_num       3836 non-null   int64         
 12  course_par       3836 non-null   int64         
 13  start_hole       3836 non-null   int64         
 14  teetime          3836 non-null   object      

In [72]:
test_df['fin_num'] = test_df['fin_text'].str.extract('(\d+)')
test_df.loc[test_df['fin_num'].isna(), 'fin_num'] = '0'
test_df['fin_num'] = test_df['fin_num'].astype(int)
test_df = test_df.drop(['fin_text'], axis=1)

In [73]:
test_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3836 entries, 0 to 4937
Data columns (total 33 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   tour             3836 non-null   object        
 1   year             3836 non-null   int64         
 2   season           3836 non-null   int64         
 3   event_completed  3836 non-null   datetime64[ns]
 4   event_name       3836 non-null   object        
 5   event_id         3836 non-null   int64         
 6   player_name      3836 non-null   object        
 7   dg_id            3836 non-null   int64         
 8   round_num        3836 non-null   int64         
 9   course_name      3836 non-null   object        
 10  course_num       3836 non-null   int64         
 11  course_par       3836 non-null   int64         
 12  start_hole       3836 non-null   int64         
 13  teetime          3836 non-null   object        
 14  round_score      3836 non-null   int64       

In [74]:
#
test_df['teetime_cleaned'] = pd.to_datetime(test_df['teetime'], format='%I:%M%p').dt.time
test_df['teetime_numeric'] = test_df['teetime_cleaned'].apply(lambda x: x.hour + x.minute / 60)
test_df = test_df.drop(['teetime','teetime_cleaned'], axis=1)

In [75]:
test_df['ohe_win'] = np.where(test_df['fin_num'] == 1, 1, 0)
test_df['ohe_top_five'] = np.where(test_df['fin_num'] <= 5, 1, 0)
test_df['ohe_top_ten'] = np.where(test_df['fin_num'] <= 10, 1, 0)
test_df['ohe_top_twenty'] = np.where(test_df['fin_num'] <= 20, 1, 0)
test_df['ohe_make_cut'] = np.where(test_df['fin_num'] == 0, 1, 0)

In [76]:
test_df_sorted = test_df.sort_values(by=['year', 'dg_id','round_completed'], ascending=[True,True,True])

In [77]:
test_df_sorted['L20_moving_avg_sg_putt'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_sg_putt'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_sg_putt'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_sg_putt'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_sg_putt'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_sg_arg'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_sg_arg'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_sg_arg'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_sg_arg'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_sg_arg'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_sg_app'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_sg_app'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_sg_app'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_sg_app'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_sg_app'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_sg_ott'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_sg_ott'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_sg_ott'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_sg_ott'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_sg_ott'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_sg_t2g'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_sg_t2g'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_sg_t2g'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_sg_t2g'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_sg_t2g'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_sg_total'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_sg_total'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_sg_total'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_sg_total'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_sg_total'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_driving_dist'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_driving_dist'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_driving_dist'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_driving_dist'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_driving_dist'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_driving_acc'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_driving_acc'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_driving_acc'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_driving_acc'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_driving_acc'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_gir'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_gir'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_gir'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_gir'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_gir'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())


test_df_sorted['L20_moving_avg_scrambling'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg_scrambling'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg_scrambling'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg_scrambling'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg_scrambling'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())

In [78]:
test_df_sorted['career_avg'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).mean())
test_df_sorted['L20_moving_avg'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).mean())
test_df_sorted['L16_moving_avg'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).mean())
test_df_sorted['L12_moving_avg'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).mean())
test_df_sorted['L8_moving_avg'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).mean())
test_df_sorted['L4_moving_avg'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).mean())

test_df_sorted['career_min'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).min())
test_df_sorted['L20_moving_min'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).min())
test_df_sorted['L16_moving_min'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).min())
test_df_sorted['L12_moving_min'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).min())
test_df_sorted['L8_moving_min'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).min())
test_df_sorted['L4_moving_min'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).min())

test_df_sorted['career_max'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).max())
test_df_sorted['L20_moving_max'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).max())
test_df_sorted['L16_moving_max'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).max())
test_df_sorted['L12_moving_max'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).max())
test_df_sorted['L8_moving_max'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).max())
test_df_sorted['L4_moving_max'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).max())

In [79]:
# test_df_sorted['career_round_score_std_dev'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_round_score_std_dev'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_round_score_std_dev'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_round_score_std_dev'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_round_score_std_dev'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_round_score_std_dev'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_sg_putt_std_dev'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_sg_putt_std_dev'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16__sg_putt_std_dev'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_putt_std_dev'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_putt_std_dev'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_sg_putt_std_dev'] = test_df_sorted.groupby('player_name')['sg_putt'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_sg_arg_std_dev'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_sg_arg_std_dev'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_sg_arg_std_dev'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_sg_arg_std_dev'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_sg_arg_std_dev'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_sg_arg_std_dev'] = test_df_sorted.groupby('player_name')['sg_arg'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_sg_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_sg_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_sg_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_sg_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_sg_ott_std_dev'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_sg_ott_std_dev'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_sg_ott_std_dev'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_sg_ott_std_dev'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_sg_ott_std_dev'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_sg_ott_std_dev'] = test_df_sorted.groupby('player_name')['sg_ott'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_sg_t2g_std_dev'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_sg_t2g_std_dev'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_sg_t2g_std_dev'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_sg_t2g_std_dev'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_sg_t2g_std_dev'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_sg_t2g_std_dev'] = test_df_sorted.groupby('player_name')['sg_t2g'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_sg_total_std_dev'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_sg_total_std_dev'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_sg_total_std_dev'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_sg_total_std_dev'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_total_std_dev'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_sg_total_std_dev'] = test_df_sorted.groupby('player_name')['sg_total'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_driving_dist_std_dev'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_driving_dist_std_dev'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_driving_dist_std_dev'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_driving_dist_std_dev'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_driving_dist_std_dev'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_driving_dist_std_dev'] = test_df_sorted.groupby('player_name')['driving_dist'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_driving_acc_std_dev'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_driving_acc_std_dev'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_driving_acc_std_dev'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_driving_acc_std_dev'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_driving_acc_std_dev'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_driving_acc_std_dev'] = test_df_sorted.groupby('player_name')['driving_acc'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_gir_std_dev'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_gir_std_dev'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_gir_std_dev'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_gir_std_dev'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_gir_std_dev'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_gir_std_dev'] = test_df_sorted.groupby('player_name')['gir'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

# test_df_sorted['career_scrambling_std_dev'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.expanding(min_periods=1).std())
test_df_sorted['L20_scrambling_std_dev'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=20, min_periods=1).std())
test_df_sorted['L16_scrambling_std_dev'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=16, min_periods=1).std())
test_df_sorted['L12_scrambling_std_dev'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
test_df_sorted['L8_scrambling_std_dev'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=8, min_periods=1).std())
test_df_sorted['L4_scrambling_std_dev'] = test_df_sorted.groupby('player_name')['scrambling'].transform(lambda x: x.rolling(window=4, min_periods=1).std())

/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/762480854.py:25: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_df_sorted['L12_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=12, min_periods=1).std())
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/762480854.py:26: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_df_sorted['L8_sg_app_std_dev'] = test_df_sorted.groupby('player_name')['sg_app'].transform(lambda x: x.rolling(window=8, min_p

In [80]:
# test_df_sorted['career_rounds_played'] = test_df_sorted.groupby('player_name')['round_score'].transform(lambda x: x.expanding(min_periods=1).count())

In [81]:
now = datetime.now()

# Calculate days since each round
test_df_sorted['Days_Since'] = (now - test_df_sorted['round_completed']).dt.days

test_df_sorted['Last_365_Days'] = np.where(test_df_sorted['Days_Since'] <= 365, 1, 0)
test_df_sorted['Last_180_Days'] = np.where(test_df_sorted['Days_Since'] <= 180, 1, 0)
test_df_sorted['Last_90_Days'] = np.where(test_df_sorted['Days_Since'] <= 90, 1, 0)
test_df_sorted['Last_60_Days'] = np.where(test_df_sorted['Days_Since'] <= 60, 1, 0)
test_df_sorted['Last_30_Days'] = np.where(test_df_sorted['Days_Since'] <= 30, 1, 0)
test_df_sorted['Last_10_Days'] = np.where(test_df_sorted['Days_Since'] <= 10, 1, 0)
test_df_sorted['Last_5_Days'] = np.where(test_df_sorted['Days_Since'] <= 5, 1, 0)

/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2011406118.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_df_sorted['Days_Since'] = (now - test_df_sorted['round_completed']).dt.days
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2011406118.py:6: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_df_sorted['Last_365_Days'] = np.where(test_df_sorted['Days_Since'] <= 365, 1, 0)
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/2011406118.py:7: PerformanceWarning: DataFrame

In [82]:
test_df_sorted.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3836 entries, 2240 to 2824
Columns: 169 entries, tour to Last_5_Days
dtypes: datetime64[ns](2), float64(138), int32(2), int64(23), object(4)
memory usage: 4.9+ MB


In [83]:
test_df_sorted['lagged_year'] = test_df_sorted.groupby('dg_id')['year'].shift(1)
test_df_sorted['lagged_season'] = test_df_sorted.groupby('dg_id')['season'].shift(1)
test_df_sorted['lagged_event_id'] = test_df_sorted.groupby('dg_id')['event_id'].shift(1)
test_df_sorted['lagged_round_num'] = test_df_sorted.groupby('dg_id')['round_num'].shift(1)
test_df_sorted['lagged_course_num'] = test_df_sorted.groupby('dg_id')['course_num'].shift(1)
test_df_sorted['lagged_course_par'] = test_df_sorted.groupby('dg_id')['course_par'].shift(1)
test_df_sorted['lagged_start_hole'] = test_df_sorted.groupby('dg_id')['start_hole'].shift(1)
test_df_sorted['lagged_round_score'] = test_df_sorted.groupby('dg_id')['round_score'].shift(1)
test_df_sorted['lagged_sg_putt'] = test_df_sorted.groupby('dg_id')['sg_putt'].shift(1)
test_df_sorted['lagged_sg_arg'] = test_df_sorted.groupby('dg_id')['sg_arg'].shift(1)
test_df_sorted['lagged_sg_app'] = test_df_sorted.groupby('dg_id')['sg_app'].shift(1)
test_df_sorted['lagged_sg_ott'] = test_df_sorted.groupby('dg_id')['sg_ott'].shift(1)
test_df_sorted['lagged_sg_t2g'] = test_df_sorted.groupby('dg_id')['sg_t2g'].shift(1)
test_df_sorted['lagged_sg_total'] = test_df_sorted.groupby('dg_id')['sg_total'].shift(1)
test_df_sorted['lagged_driving_dist'] = test_df_sorted.groupby('dg_id')['driving_dist'].shift(1)
test_df_sorted['lagged_driving_acc'] = test_df_sorted.groupby('dg_id')['driving_acc'].shift(1)
test_df_sorted['lagged_gir'] = test_df_sorted.groupby('dg_id')['gir'].shift(1)
test_df_sorted['lagged_scrambling'] = test_df_sorted.groupby('dg_id')['scrambling'].shift(1)
test_df_sorted['lagged_prox_rgh'] = test_df_sorted.groupby('dg_id')['prox_rgh'].shift(1)
test_df_sorted['lagged_prox_fw'] = test_df_sorted.groupby('dg_id')['prox_fw'].shift(1)
test_df_sorted['lagged_great_shots'] = test_df_sorted.groupby('dg_id')['great_shots'].shift(1)
test_df_sorted['lagged_poor_shots'] = test_df_sorted.groupby('dg_id')['poor_shots'].shift(1)
test_df_sorted['lagged_month'] = test_df_sorted.groupby('dg_id')['month'].shift(1)
test_df_sorted['lagged_day'] = test_df_sorted.groupby('dg_id')['day'].shift(1)
test_df_sorted['lagged_fin_num'] = test_df_sorted.groupby('dg_id')['fin_num'].shift(1)
test_df_sorted['lagged_teetime_numeric'] = test_df_sorted.groupby('dg_id')['teetime_numeric'].shift(1)
test_df_sorted['lagged_ohe_win'] = test_df_sorted.groupby('dg_id')['ohe_win'].shift(1)
test_df_sorted['lagged_ohe_top_five'] = test_df_sorted.groupby('dg_id')['ohe_top_five'].shift(1)
test_df_sorted['lagged_ohe_top_ten'] = test_df_sorted.groupby('dg_id')['ohe_top_ten'].shift(1)
test_df_sorted['lagged_ohe_top_twenty'] = test_df_sorted.groupby('dg_id')['ohe_top_twenty'].shift(1)
test_df_sorted['lagged_ohe_make_cut'] = test_df_sorted.groupby('dg_id')['ohe_make_cut'].shift(1)

/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/3969898397.py:1: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_df_sorted['lagged_year'] = test_df_sorted.groupby('dg_id')['year'].shift(1)
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/3969898397.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_df_sorted['lagged_season'] = test_df_sorted.groupby('dg_id')['season'].shift(1)
/var/folders/v_/6t_lr7fd57703dfgsj3k_p9h0000gn/T/ipykernel_19642/3969898397.py:3: PerformanceWarning: DataFrame 

In [84]:
test_df_sorted.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3836 entries, 2240 to 2824
Columns: 200 entries, tour to lagged_ohe_make_cut
dtypes: datetime64[ns](2), float64(169), int32(2), int64(23), object(4)
memory usage: 5.9+ MB


In [85]:
test_df_sorted.isna().sum()

tour                             0
year                             0
season                           0
event_completed                  0
event_name                       0
event_id                         0
player_name                      0
dg_id                            0
round_num                        0
course_name                      0
course_num                       0
course_par                       0
start_hole                       0
round_score                      0
sg_putt                          0
sg_arg                           0
sg_app                           0
sg_ott                           0
sg_t2g                           0
sg_total                         0
driving_dist                     0
driving_acc                      0
gir                              0
scrambling                       0
prox_rgh                         0
prox_fw                          0
great_shots                      0
poor_shots                       0
round_completed     

In [86]:
test_df_sorted = test_df_sorted.dropna(axis=0)

In [87]:
test_df_sorted.isna().sum()

tour                           0
year                           0
season                         0
event_completed                0
event_name                     0
event_id                       0
player_name                    0
dg_id                          0
round_num                      0
course_name                    0
course_num                     0
course_par                     0
start_hole                     0
round_score                    0
sg_putt                        0
sg_arg                         0
sg_app                         0
sg_ott                         0
sg_t2g                         0
sg_total                       0
driving_dist                   0
driving_acc                    0
gir                            0
scrambling                     0
prox_rgh                       0
prox_fw                        0
great_shots                    0
poor_shots                     0
round_completed                0
month                          0
day       

In [88]:
test_df_sorted.loc[test_df_sorted['player_name'] == 'Scheffler, Scottie',]

tour  year  season event_completed  \
61    pga  2024    2024      2024-01-07   
60    pga  2024    2024      2024-01-07   
72    pga  2024    2024      2024-01-07   
812   pga  2024    2024      2024-01-21   
760   pga  2024    2024      2024-01-21   
1750  pga  2024    2024      2024-02-04   
1762  pga  2024    2024      2024-02-04   
2285  pga  2024    2024      2024-02-11   
2284  pga  2024    2024      2024-02-11   
2283  pga  2024    2024      2024-02-11   
2282  pga  2024    2024      2024-02-11   
2441  pga  2024    2024      2024-02-18   
2440  pga  2024    2024      2024-02-18   
2439  pga  2024    2024      2024-02-18   
2438  pga  2024    2024      2024-02-18   
3896  pga  2024    2024      2024-03-10   
3897  pga  2024    2024      2024-03-10   
3898  pga  2024    2024      2024-03-10   
3899  pga  2024    2024      2024-03-10   
4471  pga  2024    2024      2024-03-17   
4472  pga  2024    2024      2024-03-17   
4477  pga  2024    2024      2024-03-17   
4474  pga  2024    2024      2024-03-17   

                                             event_name  event_id  \
61                                           The Sentry        16   
60                                           The Sentry        16   
72                                           The Sentry        16   
812                                The American Express         2   
760                                The American Express         2   
1750                           AT&T Pebble Beach Pro-Am         5   
1762                           AT&T Pebble Beach Pro-Am         5   
2285                                    WM Phoenix Open         3   
2284                                    WM Phoenix Open         3   
2283                                    WM Phoenix Open         3   
2282                                    WM Phoenix Open         3   
2441                           The Genesis Invitational         7   
2440                           The Genesis Invitational         7   
2439                           The Genesis Invitational         7   
2438                           The Genesis Invitational         7   
3896  Arnold Palmer Invitational presented by Master...         9   
3897  Arnold Palmer Invitational presented by Master...         9   
3898  Arnold Palmer Invitational presented by Master...         9   
3899  Arnold Palmer Invitational presented by Master...         9   
4471                           THE PLAYERS Championship        11   
4472                           THE PLAYERS Championship        11   
4477                           THE PLAYERS Championship        11   
4474                           THE PLAYERS Championship        11   

             player_name  dg_id  round_num  \
61    Scheffler, Scottie  18417          2   
60    Scheffler, Scottie  18417          3   
72    Scheffler, Scottie  18417          4   
812   Scheffler, Scottie  18417          3   
760   Scheffler, Scottie  18417          4   
1750  Scheffler, Scottie  18417          2   
1762  Scheffler, Scottie  18417          3   
2285  Scheffler, Scottie  18417          1   
2284  Scheffler, Scottie  18417          2   
2283  Scheffler, Scottie  18417          3   
2282  Scheffler, Scottie  18417          4   
2441  Scheffler, Scottie  18417          1   
2440  Scheffler, Scottie  18417          2   
2439  Scheffler, Scottie  18417          3   
2438  Scheffler, Scottie  18417          4   
3896  Scheffler, Scottie  18417          1   
3897  Scheffler, Scottie  18417          2   
3898  Scheffler, Scottie  18417          3   
3899  Scheffler, Scottie  18417          4   
4471  Scheffler, Scottie  18417          1   
4472  Scheffler, Scottie  18417          2   
4477  Scheffler, Scottie  18417          3   
4474  Scheffler, Scottie  18417          4   

                                    course_name  course_num  course_par  \
61                 Plantation Course at Kapalua         656          73   
60                 Plantation Course at Kapalua         656 

***

In [89]:
train_df_sorted.info()
test_df_sorted.info()

<class 'pandas.core.frame.DataFrame'>
Index: 97157 entries, 165 to 128293
Columns: 200 entries, tour to lagged_ohe_make_cut
dtypes: datetime64[ns](2), float64(170), int32(2), int64(22), object(4)
memory usage: 148.2+ MB
<class 'pandas.core.frame.DataFrame'>
Index: 3571 entries, 2241 to 2824
Columns: 200 entries, tour to lagged_ohe_make_cut
dtypes: datetime64[ns](2), float64(169), int32(2), int64(23), object(4)
memory usage: 5.4+ MB


In [90]:
current_df = test_df_sorted.copy()

***

***

# Linear Regression

In [91]:
train_df_sorted = train_df_sorted.drop(['tour','event_name','course_name','player_name','round_completed','event_completed','year'
                                        ,'season','event_completed','event_id','dg_id','round_num','course_num','course_par'
                                        ,'start_hole','sg_putt','sg_arg','sg_app','sg_ott','sg_t2g','sg_total','driving_dist'
                                        ,'driving_acc','gir','scrambling','prox_rgh','prox_fw','great_shots','poor_shots'
                                        ,'round_completed','month','day','fin_num','teetime_numeric','ohe_win','ohe_top_five'
                                        ,'ohe_top_ten','ohe_top_twenty','ohe_make_cut'], axis=1)

test_df_sorted = test_df_sorted.drop(['tour','event_name','course_name','player_name','round_completed','event_completed','year'
                                        ,'season','event_completed','event_id','dg_id','round_num','course_num','course_par'
                                        ,'start_hole','sg_putt','sg_arg','sg_app','sg_ott','sg_t2g','sg_total','driving_dist'
                                        ,'driving_acc','gir','scrambling','prox_rgh','prox_fw','great_shots','poor_shots'
                                        ,'round_completed','month','day','fin_num','teetime_numeric','ohe_win','ohe_top_five'
                                        ,'ohe_top_ten','ohe_top_twenty','ohe_make_cut'], axis=1)

In [92]:
train_df_sorted.head()

round_score  L20_moving_avg_sg_putt  L16_moving_avg_sg_putt  \
165           70.0                 -1.0040                 -1.0040   
11941         68.0                 -0.8235                 -0.8235   
7151          78.0                  1.9860                  1.9860   
180           65.0                 -0.8120                 -0.8120   
179           70.0                 -0.6270                 -0.6270   

       L12_moving_avg_sg_putt  L8_moving_avg_sg_putt  L4_moving_avg_sg_putt  \
165                   -1.0040                -1.0040                -1.0040   
11941                 -0.8235                -0.8235                -0.8235   
7151                   1.9860                 1.9860                 1.9860   
180                   -0.8120                -0.8120                -0.8120   
179                   -0.6270                -0.6270                -0.6270   

       L20_moving_avg_sg_arg  L16_moving_avg_sg_arg  L12_moving_avg_sg_arg  \
165                -0.247000              -0.247000              -0.247000   
11941              -0.210000              -0.210000              -0.210000   
7151               -1.498000              -1.498000              -1.498000   
180                 1.266500               1.266500               1.266500   
179                 0.596667               0.596667               0.596667   

       L8_moving_avg_sg_arg  L4_moving_avg_sg_arg  L20_moving_avg_sg_app  \
165               -0.247000             -0.247000               2.057000   
11941             -0.210000             -0.210000               0.207500   
7151              -1.498000             -1.498000              -1.753500   
180                1.266500              1.266500               0.176000   
179                0.596667              0.596667               0.512667   

       L16_moving_avg_sg_app  L12_moving_avg_sg_app  L8_moving_avg_sg_app  \
165                 2.057000               2.057000              2.057000   
11941               0.207500               0.207500              0.207500   
7151               -1.753500              -1.753500             -1.753500   
180                 0.176000               0.176000              0.176000   
179                 0.512667               0.512667              0.512667   

       L4_moving_avg_sg_app  L20_moving_avg_sg_ott  L16_moving_avg_sg_ott  \
165                2.057000              -0.469000              -0.469000   
11941              0.207500               0.024000               0.024000   
7151              -1.753500              -0.233000              -0.233000   
180                0.176000              -0.322000              -0.322000   
179                0.512667              -0.841333              -0.841333   

       L12_moving_avg_sg_ott  L8_moving_avg_sg_ott  L4_moving_avg_sg_ott  \
165                -0.469000             -0.469000             -0.469000   
11941               0.024000              0.024000              0.024000   
7151               -0.233000             -0.233000             -0.233000   
180                -0.322000             -0.322000             -0.322000   
179                -0.841333             -0.841333             -0.841333   

       L20_moving_avg_sg_t2g  L16_moving_avg_sg_t2g  L12_moving_avg_sg_t2g  \
165                 1.341000               1.341000               1.341000   
11941               0.020500               0.020500               0.020500   
7151               -3.485500              -3.485500              -3.485500   
180                 1.121000               1.121000               1.121000   
179                 0.268333               0.268333               0.268333   

       L8_moving_avg_sg_t2g  L4_moving_avg_sg_t2g  L20_moving_avg_sg_total  \
165                1.341000              1.341000                   0.3365   
11941              0.020500              0.020500                  -0.8030   
7151              -3.485500             -3.485500                  -1.4995   
180                1.

In [93]:
X_train = train_df_sorted.drop(['round_score'], axis=1)
y_train = train_df_sorted['round_score']


scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)

model = LinearRegression()
model.fit(X_train_scaled, y_train)

r2_train = model.score(X_train_scaled,y_train)

X_train_pred = model.predict(X_train_scaled)
mape_train = mean_absolute_percentage_error(X_train_pred,y_train)

print(f' Train: \n r2: {r2_train:.4f} \n mape: {mape_train:.4f}')

 Train: 
 r2: 0.4592 
 mape: 0.0270


# Lasso Regression

In [ ]:
lasso_model = Lasso() 
lasso_model.fit(X_train_scaled, y_train)

l_r2_train = lasso_model.score(X_train_scaled,y_train)
l_r2_test = lasso_model.score(X_test_scaled,y_test)

l_X_train_pred = lasso_model.predict(X_train_scaled)
l_X_test_pred = lasso_model.predict(X_test_scaled)
l_mape_train = mean_absolute_percentage_error(l_X_train_pred,y_train)
l_mape_test = mean_absolute_percentage_error(l_X_test_pred,y_test)

print(f' Train: \n r2: {l_r2_train:.4f} \n mape: {l_mape_train:.4f}')
print(f' Test: \n r2: {l_r2_test:.4f} \n mape: {l_mape_test:.4f}')

# Ridge Regression

In [ ]:
ridge_model = Ridge() 
ridge_model.fit(X_train_scaled, y_train)

r_r2_train = ridge_model.score(X_train_scaled,y_train)
r_r2_test = ridge_model.score(X_test_scaled,y_test)

r_X_train_pred = ridge_model.predict(X_train_scaled)
r_X_test_pred = ridge_model.predict(X_test_scaled)
r_mape_train = mean_absolute_percentage_error(r_X_train_pred,y_train)
r_mape_test = mean_absolute_percentage_error(r_X_test_pred,y_test)

print(f' Train: \n r2: {r_r2_train:.4f} \n mape: {r_mape_train:.4f}')
print(f' Test: \n r2: {r_r2_test:.4f} \n mape: {r_mape_test:.4f}')

# Linear Pipeline

In [ ]:
estimators = [('scaler', StandardScaler()),
              ('reduce_dim', PCA(n_components=0.9)),
              ('model', LinearRegression())]


pipe = Pipeline(estimators)
param_grid = [{'scaler':[StandardScaler(), MinMaxScaler()],
               'reduce_dim':[None,PCA(n_components=0.9)],
               'model':[Lasso(max_iter=int(1e9))],
               'model__alpha':np.logspace(-3,3,50)},
              {'scaler':[StandardScaler(), MinMaxScaler()],
               'reduce_dim':[None,PCA(n_components=0.9)],
               'model':[Ridge(max_iter=int(1e9))],
               'model__alpha':np.logspace(0,10,50)},
             {'scaler':[StandardScaler(), MinMaxScaler()],
              'reduce_dim':[None,PCA(n_components=0.9)],
              'model':[LinearRegression()]}
             ]

grid = GridSearchCV(pipe, param_grid,n_jobs=-1,verbose=20,
                    scoring=["r2","neg_mean_absolute_percentage_error"],refit='r2')
                   
fittedgrid = grid.fit(X_train, y_train)

In [ ]:
results = pd.DataFrame(fittedgrid.cv_results_)

In [ ]:
str(results.loc[0,"param_model"])

In [ ]:
results.param_model.value_counts()

In [ ]:
lasso_sel = results["param_model"].apply(lambda x:str(x).startswith("Lasso"))

In [ ]:
lasso_results = results.loc[lasso_sel,["param_model__alpha","mean_test_r2","mean_test_neg_mean_absolute_percentage_error"]]
plt.figure()
plt.plot(lasso_results["param_model__alpha"],lasso_results["mean_test_r2"])
plt.xscale("log")
plt.xlabel("alpha")
plt.ylabel("R2")
ax2 = plt.gca().twinx()
ax2.plot(lasso_results["param_model__alpha"],lasso_results["mean_test_neg_mean_absolute_percentage_error"],color='red')

In [ ]:
ridge_sel = results["param_model"].apply(lambda x:str(x).startswith("Ridge"))

In [ ]:
ridge_results = results.loc[ridge_sel,["param_model__alpha","mean_test_r2","mean_test_neg_mean_absolute_percentage_error"]]
plt.figure()
plt.plot(ridge_results["param_model__alpha"],ridge_results["mean_test_r2"])
plt.xscale("log")
plt.xlabel("alpha")
plt.ylabel("R2")
ax2 = plt.gca().twinx()
ax2.plot(ridge_results["param_model__alpha"],ridge_results["mean_test_neg_mean_absolute_percentage_error"],color='red')

In [ ]:
fittedgrid.best_estimator_

In [ ]:
fittedgrid.best_estimator_.get_params()

In [ ]:
fittedgrid.best_estimator_.score(X_test,y_test)

In [ ]:
field_df[['dg_id','player_name','current_round','event_name']].sort_values(by='player_name', ascending=True)

# Random Forest

In [ ]:
estimators2 = [('scaler', StandardScaler()),
              ('reduce_dim', PCA(n_components=0.9)),
              ('model', RandomForestRegressor())]


pipe2 = Pipeline(estimators2)
param_grid2 = [{'scaler': [StandardScaler(), MinMaxScaler()],
                'reduce_dim': [None, PCA(n_components=0.9)],
                'model':[RandomForestRegressor()],
                'model__max_depth':[5,10,15,20,25]}
              ]


grid2 = GridSearchCV(pipe2, param_grid2, cv=5,verbose=20,n_jobs=-1,
                    scoring=["r2","neg_mean_absolute_percentage_error"],refit='r2')
                   
fittedgrid2 = grid2.fit(X_train, y_train)

In [ ]:
results2 = pd.DataFrame(fittedgrid2.cv_results_)

In [ ]:
results2[["param_scaler","param_reduce_dim","param_model__max_depth","mean_test_r2"]]

In [ ]:
fittedgrid2.best_estimator_

In [ ]:
fittedgrid2.best_estimator_.score(X_test,y_test)

***

***

# Model Projections

In [ ]:
most_recent_scores = current_df.sort_values('round_completed').groupby('player_name').last().reset_index()

In [ ]:
most_recent_scores.head()

In [ ]:
most_recent_scores = most_recent_scores.drop(['tour','event_name','course_name','player_name','round_completed','event_completed','year'
                                        ,'season','event_completed','event_id','round_num','course_num','course_par'
                                        ,'start_hole','sg_putt','sg_arg','sg_app','sg_ott','sg_t2g','sg_total','driving_dist'
                                        ,'driving_acc','gir','scrambling','prox_rgh','prox_fw','great_shots','poor_shots'
                                        ,'round_completed','month','day','fin_num','teetime_numeric','ohe_win','ohe_top_five'
                                        ,'ohe_top_ten','ohe_top_twenty','ohe_make_cut'], axis=1)

In [ ]:
most_recent_scores.head()

In [ ]:
most_recent_scores = most_recent_scores.set_index('dg_id')

In [ ]:
most_recent_scores.head(20)

In [ ]:
most_recent_scores = most_recent_scores.drop(['round_score'], axis=1)

In [ ]:
predicted_score = fittedgrid.best_estimator_.predict(most_recent_scores)
print(predicted_score)

In [ ]:
most_recent_scores['predicted_score'] = predicted_score

In [ ]:
most_recent_scores.head()

In [ ]:
result_df = most_recent_scores.merge(player_df[['dg_id', 'player_name']], on='dg_id', how='left')

In [ ]:
result_df.sort_values(by='predicted_score', ascending=True).head(10)

In [ ]:
this_week_df = result_df.merge(field_df[['dg_id', 'event_name']], on='dg_id', how='inner')
this_week_df.sort_values(by='predicted_score', ascending=True)

In [ ]:
tt_df.loc[tt_df['player_name'] == 'Finau, Tony'].tail()

# Neural Network

In [94]:
from sklearn.datasets import fetch_california_housing
from sklearn.neural_network import MLPRegressor
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from keras.callbacks import EarlyStopping
from keras.callbacks import ModelCheckpoint
from keras.models import load_model

In [95]:
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)

In [96]:
model = keras.Sequential()

regularizer = keras.regularizers.l1(0.001)

model.add(layers.Dense(40, activation="relu", kernel_regularizer=regularizer))
model.add(layers.Dropout(0.1))
model.add(layers.Dense(40, activation="relu", kernel_regularizer=regularizer))
model.add(layers.Dropout(0.1))
model.add(layers.Dense(40, activation="relu", kernel_regularizer=regularizer))
model.add(layers.Dropout(0.1))


model.add(layers.Dense(1))

model.compile(
    # Optimizer
    optimizer=keras.optimizers.Adam(),
    # Loss function to minimize
    loss=keras.losses.MeanSquaredError()
)


# model_checkpoint = ModelCheckpoint('best_model.h5', save_best_only=True, monitor='val_loss')
# early_stopping = EarlyStopping(monitor='val_loss', patience=50)

history = model.fit(X_train_scaled, y_train, epochs=150, verbose=1) #,validation_data=(X_val_scaled, y_val),callbacks=[early_stopping, model_checkpoint])

Epoch 1/150
   1/3037 [..............................] - ETA: 7:05 - loss: 4896.3379

2024-03-29 18:41:52.282420: W tensorflow/core/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz


3037/3037 [==============================] - 1s 319us/step - loss: 196.6795
Epoch 2/150
3037/3037 [==============================] - 1s 314us/step - loss: 43.1956
Epoch 3/150
3037/3037 [==============================] - 1s 313us/step - loss: 36.6966
Epoch 4/150
3037/3037 [==============================] - 1s 313us/step - loss: 32.8371
Epoch 5/150
3037/3037 [==============================] - 1s 314us/step - loss: 29.2999
Epoch 6/150
3037/3037 [==============================] - 1s 316us/step - loss: 26.1362
Epoch 7/150
3037/3037 [==============================] - 1s 316us/step - loss: 24.3552
Epoch 8/150
3037/3037 [==============================] - 1s 315us/step - loss: 22.9242
Epoch 9/150
3037/3037 [==============================] - 1s 322us/step - loss: 22.1783
Epoch 10/150
3037/3037 [==============================] - 1s 315us/step - loss: 21.3241
Epoch 11/150
3037/3037 [==============================] - 1s 304us/step - loss: 20.9986
Epoch 12/150
3037/3037 [============================

In [97]:
train_loss = history.history["loss"][-1]

print(f"Train Loss: {train_loss:.4f}")

Train Loss: 4.5406


# Model Projections

In [98]:
most_recent_scores = current_df.sort_values('round_completed').groupby('player_name').last().reset_index()

In [99]:
most_recent_scores = most_recent_scores.drop(['tour','event_name','course_name','player_name','round_completed','event_completed','year'
                                        ,'season','event_completed','event_id','round_num','course_num','course_par'
                                        ,'start_hole','sg_putt','sg_arg','sg_app','sg_ott','sg_t2g','sg_total','driving_dist'
                                        ,'driving_acc','gir','scrambling','prox_rgh','prox_fw','great_shots','poor_shots'
                                        ,'round_completed','month','day','fin_num','teetime_numeric','ohe_win','ohe_top_five'
                                        ,'ohe_top_ten','ohe_top_twenty','ohe_make_cut'], axis=1)

In [111]:
most_recent_scores.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 252 entries, 0 to 251
Columns: 164 entries, L20_moving_avg_sg_putt to predicted_score
dtypes: float32(1), float64(154), int64(9)
memory usage: 322.0 KB


In [101]:
player_ids = df['dg_id']
most_recent_scores = most_recent_scores.drop(['dg_id','round_score'], axis=1)

In [102]:
most_recent_scores.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 252 entries, 0 to 251
Columns: 162 entries, L20_moving_avg_sg_putt to lagged_ohe_make_cut
dtypes: float64(154), int64(8)
memory usage: 319.1 KB


In [103]:
mr_scaled = scaler.transform(most_recent_scores)

In [104]:
predicted_score = model.predict(mr_scaled)
print(predicted_score)

[[69.79415 ]
 [72.66626 ]
 [72.14854 ]
 [75.479416]
 [72.51458 ]
 [71.29649 ]
 [69.74913 ]
 [74.78484 ]
 [76.43279 ]
 [73.62517 ]
 [69.2848  ]
 [69.44518 ]
 [72.02301 ]
 [72.09602 ]
 [73.44256 ]
 [71.73834 ]
 [72.04586 ]
 [72.97085 ]
 [71.53128 ]
 [76.12525 ]
 [73.687126]
 [73.12907 ]
 [73.15369 ]
 [71.07357 ]
 [73.94833 ]
 [70.68781 ]
 [73.007484]
 [73.87251 ]
 [73.94804 ]
 [70.047775]
 [69.56957 ]
 [66.999306]
 [72.456085]
 [72.18669 ]
 [71.452805]
 [73.27517 ]
 [73.505714]
 [73.09869 ]
 [72.0413  ]
 [71.89634 ]
 [73.059   ]
 [71.80169 ]
 [74.09641 ]
 [71.41261 ]
 [69.69115 ]
 [72.06065 ]
 [71.70514 ]
 [72.3754  ]
 [71.169205]
 [72.21366 ]
 [73.49814 ]
 [75.02986 ]
 [71.80736 ]
 [71.57457 ]
 [72.32824 ]
 [75.267075]
 [71.53668 ]
 [68.43272 ]
 [72.89747 ]
 [73.37674 ]
 [69.183365]
 [70.895874]
 [78.33924 ]
 [71.82052 ]
 [70.20273 ]
 [71.86388 ]
 [68.15844 ]
 [71.71887 ]
 [73.08701 ]
 [73.873955]
 [74.1388  ]
 [73.42521 ]
 [69.55583 ]
 [73.70073 ]
 [71.168976]
 [71.39688 ]
 [71.317825]

In [105]:
most_recent_scores['dg_id'] = player_ids
most_recent_scores['predicted_score'] = predicted_score

In [106]:
result_df = most_recent_scores.merge(player_df[['dg_id', 'player_name']], on='dg_id', how='left')

In [107]:
result_df.sort_values(by='predicted_score', ascending=True).head(10)

L20_moving_avg_sg_putt  L16_moving_avg_sg_putt  L12_moving_avg_sg_putt  \
31                 0.599900                0.970375                0.626083   
192                0.063900                0.103813                0.102917   
113                0.052000                0.052000                0.052000   
112               -0.462500               -0.462500               -0.462500   
88                 0.181500                0.181500                0.181500   
66                -0.441000               -0.441000               -0.441000   
189                0.595471                0.762813                1.323667   
117               -0.340850               -0.260000               -0.400750   
57                 0.249650                0.553813                0.356833   
150               -0.166091               -0.166091               -0.166091   

     L8_moving_avg_sg_putt  L4_moving_avg_sg_putt  L20_moving_avg_sg_arg  \
31                1.375125                 1.5290               0.144700   
192               0.699125                 0.3115               0.686350   
113               0.052000                 0.0520              -0.114250   
112              -0.462500                -0.4625              -0.497000   
88                0.181500                 0.0230               0.720625   
66               -0.441000                -0.4410              -1.669000   
189               1.933625                 2.3930              -0.119176   
117              -0.477125                 1.1975               0.151100   
57                0.071250                -0.1115               0.427550   
150               0.271500                 0.4650               0.195909   

     L16_moving_avg_sg_arg  L12_moving_avg_sg_arg  L8_moving_avg_sg_arg  \
31                0.110375               0.091250              0.234875   
192               0.804375               1.157833              0.860625   
113              -0.114250              -0.114250             -0.114250   
112              -0.497000              -0.497000             -0.497000   
88                0.720625               0.720625              0.720625   
66               -1.669000              -1.669000             -1.669000   
189              -0.145250              -0.250750             -0.371500   
117               0.230438               0.083917              0.474625   
57                0.431062               0.434083              0.321875   
150               0.195909               0.195909              0.227500   

     L4_moving_avg_sg_arg  L20_moving_avg_sg_app  L16_moving_avg_sg_app  \
31                0.50725               0.815250               0.906000   
192               0.77450               1.307200               1.150063   
113              -0.11425              -0.022000              -0.022000   
112              -0.49700              -0.211500              -0.211500   
88                0.95500               0.501125               0.501125   
66               -1.66900              -0.241000              -0.241000   
189              -0.68475               0.029059               0.201313   
117               0.60875               0.534450               0.364625   
57                0.23000              -0.036650               0.137875   
150               0.10025               0.261091               0.261091   

     L12_moving_avg_sg_app  L8_moving_avg_sg_app  L4_moving_avg_sg_app  \
31                0.767167              1.126750               1.53875   
192               0.763167              1.208000               1.58800   
113              -0.022000             -0.022000              -0.02200   
112              -0.211500             -0.211500              -0.21150   
88                0.501125              0.501125               0.64200   
66               -0.241000             -0.241000              -0.24100   
189               0.008833              0.047000              -0.02425   
117               0.464583              0.731625      

In [110]:
this_week_df = result_df.merge(field_df[['dg_id', 'event_name']], on='dg_id', how='inner')
this_week_df.sort_values(by='predicted_score', ascending=True)

L20_moving_avg_sg_putt  L16_moving_avg_sg_putt  L12_moving_avg_sg_putt  \
56                0.063900                0.103813                0.102917   
44               -0.166091               -0.166091               -0.166091   
31                2.035000                2.035000                2.035000   
24                0.060100                0.302438                0.437917   
27               -0.300950               -0.251563               -0.208333   
36               -0.723350               -0.657375               -0.556583   
16                0.149500                0.149500                0.149500   
51               -0.176500               -0.176500               -0.176500   
10                1.304389                1.271750                1.132750   
0                 0.407450                0.462000                0.290750   
63                0.060750                0.060750                0.060750   
49                0.138900               -0.008000               -0.069667   
70                0.814500                0.789312                0.428833   
72                0.927100                0.959875                0.986333   
47               -0.103818               -0.103818               -0.103818   
30                0.177050                0.157500                0.305167   
84               -0.785316               -0.973250               -1.006667   
33               -1.252000               -1.252000               -1.252000   
25                0.268000                0.268000                0.335667   
83               -0.500900               -0.615500               -0.451917   
81                0.256800                0.168625                0.071167   
20               -0.442250               -0.442250               -0.442250   
62                0.260312                0.260312                0.467000   
9                -0.726500               -0.726500               -0.726500   
40                0.690667                0.690667                0.690667   
14                0.278600                0.255312                0.383667   
61                0.143611                0.185937                0.375750   
48               -1.238842               -1.172250               -1.204083   
15               -1.613833               -1.613833               -1.613833   
60                0.227950                0.060688               -0.091000   
73               -0.476600               -0.610875               -0.844083   
18                0.146100                0.070438               -0.159250   
13               -0.950842               -1.033625               -1.040917   
57               -0.546714               -0.546714               -0.616667   
37                0.597200                0.556063                0.406667   
80                0.211750                0.211750                0.249917   
67               -0.653412               -0.648750               -0.752000   
17               -0.610250               -0.610250               -0.610250   
5                 0.310900                0.182875                0.071333   
21               -0.278500               -0.278500               -0.278500   
76               -0.444625               -0.444625               -0.939833   
85               -0.027500               -0.027500                0.305167   
19               -0.134000               -0.134000               -0.134000   
43               -0.584000               -0.584000               -0.584000   
68               -0.852300               -0.852300               -0.852300   
77               -0.395154               -0.395154               -0.219500   
8                -2.160000               -2.160000               -2.160000   
32               -0.347100               -0.379750               -0.624833   
65                0.034895               -0.154188                0.090083   
4                -1.424500               -1.424500               -1.424500   
38               -0.002714

# **^FIX THE DUPLICATE PLAYERS ABOVE^**

***

***

# Export

In [ ]:
this_week_df.to_csv('this_week_df.csv', index=False)

In [ ]:
np.savetxt("pds.csv", predicted_score, delimiter=",")

***

# Citations

- Documentation:
    - https://pandas.pydata.org/docs/reference/api/pandas.io.formats.style.Styler.set_sticky.html
    - https://towardsdatascience.com/10-useful-jupyter-notebook-extensions-for-a-data-scientist-bd4cb472c25e
- ChatGPT:
    - "Subtracting an integer from a date column in pandas based on conditions where we would use nested ifs"

***

# Archive Code

In [ ]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression


preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), ['event_id', 'course_num', 'course_par', 'round_num', 'teetime_numeric', 'start_hole', 'fin_num', 'sg_putt', 'sg_arg', 'sg_app',
                                   'sg_ott', 'sg_t2g', 'sg_total', 'driving_dist', 'driving_acc', 'gir', 'scrambling', 'prox_rgh', 'prox_fw', 'great_shots', 'poor_shots',
                                   'L20_moving_avg', 'L10_moving_avg', 'L5_moving_avg']),
        ('binary', 'passthrough',['ohe_win', 'ohe_top_five', 'ohe_top_ten', 'ohe_top_twenty', 'ohe_make_cut'])
    ]
)


In [ ]:
# data_features = df_sorted.drop(['dg_id','tour','year','event_name','course_name','player_name','round_completed','event_completed'], axis=1)
# X_train_processed = preprocessor.fit_transform(X_train)
# X_test_processed = preprocessor.transform(X_test)

In [ ]:
# windows = [
#     ('last_30_days', 30, 1.0),  # (Name, Days in window, Weight)
#     ('last_90_days', 90, 0.3),
#     ('last_365_days', 365, 0.1),
#     ('older', float('inf'), 0)  # Use inf for older than 365 days
# ]

# # Initialize a column for weights
# df_sorted['weights'] = 0.25  # Default weight for older data

# for window_name, window_days, weight in windows[::-1]:
#     # Apply weights based on the days since
#     df_sorted.loc[df_sorted['Days_Since'] <= window_days, 'weights'] = weight


# ,'weights'
# weights = df_sorted['weights']
# , weights_train, weights_test, weights
# , sample_weight=weights_train)
# , sample_weight=weights_train))
# , sample_weight=weights_test))

In [ ]:
# Add rolling total of rounds prior to the specific record in the dataframe